In [1]:
import numpy as np

import sys
sys.path.append("../")
from koopmanlib.dictionary import PsiNN

In [2]:
basis_function = PsiNN(layer_sizes=[100,100,100], n_psi_train=100)

In [3]:
from duffing_oscillator import duffing_oscillator
from scipy.integrate import solve_ivp

# Parameters
delta = 0.5
alpha = -1
beta = 1

# Sample N=1000 initial points, with uniform distribution [-2, 2].
N = 1000
np.random.seed(39)
sample_data_x0 = (np.random.rand(N, 2) * 4) - 2

tspan = [0, 2.5]
nstep = 11
data = np.zeros((N, 2, nstep))

t_eval = np.linspace(tspan[0], tspan[1], nstep)

for idx, x0 in enumerate(sample_data_x0):
    sol = solve_ivp(duffing_oscillator, tspan, x0, t_eval=t_eval, args=(delta, alpha, beta))
    data[idx, 0, :] = sol.y[0]
    data[idx, 1, :] = sol.y[1]

# Pairwise shifted data X and Y
X = data[:, :, :-1] # shape: (1000, 2, 10)
Y = data[:, :, 1:]
print(X.shape, type(X))
print(Y.shape, type(Y))

# Transpose and reshape the data.
X = np.transpose(X, (0, 2, 1)).reshape(N * (nstep-1), 2) # shape: (10000, 2)
Y = np.transpose(Y, (0, 2, 1)).reshape(N * (nstep-1), 2)
print(X.shape, type(X))
print(Y.shape, type(Y))

(1000, 2, 10) <class 'numpy.ndarray'>
(1000, 2, 10) <class 'numpy.ndarray'>
(10000, 2) <class 'numpy.ndarray'>
(10000, 2) <class 'numpy.ndarray'>


In [4]:
len_all = X.shape[0]
data_x_train = X[:int(0.7*len_all),:]
data_x_valid = X[int(0.7*len_all)+1:,:]

data_y_train = Y[:int(0.7*len_all),:]
data_y_valid = Y[int(0.7*len_all)+1:,:]

In [5]:
data_train = [data_x_train, data_y_train]
data_valid = [data_x_valid, data_y_valid]

In [6]:
from koopmanlib.solver_0 import KoopmanDLSolver # resDMD solver using regression
solver = KoopmanDLSolver(dic=basis_function,
                         target_dim=np.shape(data_train)[-1],
                         reg=0.1)

solver.build(data_train=data_train,
             data_valid=data_valid,
             epochs=3000,
             batch_size=5000,
             lr=1e-6,
             log_interval=10,
             lr_decay_factor=.8)

Epoch 1/2
2/2 [==============================] - 1s 196ms/step - loss: 1.6920e-05 - val_loss: 2.0985e-05
Epoch 2/2
2/2 [==============================] - 0s 40ms/step - loss: 1.6962e-05 - val_loss: 2.0896e-05
number of the outer loop: 0
Epoch 1/2
2/2 [==============================] - 0s 62ms/step - loss: 1.6869e-05 - val_loss: 2.0770e-05
Epoch 2/2
2/2 [==============================] - 0s 38ms/step - loss: 1.6891e-05 - val_loss: 2.0778e-05
number of the outer loop: 1
Epoch 1/2
2/2 [==============================] - 0s 61ms/step - loss: 1.6852e-05 - val_loss: 2.0883e-05
Epoch 2/2
2/2 [==============================] - 0s 40ms/step - loss: 1.6866e-05 - val_loss: 2.0852e-05
number of the outer loop: 2
Epoch 1/2
2/2 [==============================] - 0s 61ms/step - loss: 1.6837e-05 - val_loss: 2.0747e-05
Epoch 2/2
2/2 [==============================] - 0s 43ms/step - loss: 1.6828e-05 - val_loss: 2.0736e-05
number of the outer loop: 3
Epoch 1/2
2/2 [==============================] - 0s 61m

In [7]:
evalues = solver.eigenvalues.T
efuns = solver.eigenfunctions(X)
kpm_modes = solver.compute_mode().T
N_dict = np.shape(evalues)[0]

resDMD_DL_outputs0 = {
    'resDMD_DL_outputs':{
    'efuns': efuns,
    'evalues': evalues,
    'kpm_modes': kpm_modes,
    'N_dict':N_dict
    }
}

print(resDMD_DL_outputs0['resDMD_DL_outputs']['evalues'])
print(resDMD_DL_outputs0['resDMD_DL_outputs']['efuns'].shape)

[ 1.01412498e+00+0.00000000e+00j  9.99998623e-01+0.00000000e+00j
  8.43234458e-01+1.55085089e-01j  8.43234458e-01-1.55085089e-01j
  7.72214055e-01-3.75114126e-01j  7.72214055e-01+3.75114126e-01j
  6.54798269e-01-2.95601680e-01j  6.54798269e-01+2.95601680e-01j
  4.46800059e-01+4.98377599e-01j  4.46800059e-01-4.98377599e-01j
  2.69915010e-01+7.72949847e-02j  2.69915010e-01-7.72949847e-02j
  1.76604312e-01-6.79175517e-01j  1.76604312e-01+6.79175517e-01j
  8.01815012e-02-1.79426709e-01j  8.01815012e-02+1.79426709e-01j
  3.46395788e-02+0.00000000e+00j  1.51867783e-02+0.00000000e+00j
  1.05349456e-02-3.27224314e-03j  1.05349456e-02+3.27224314e-03j
  4.06169920e-03+0.00000000e+00j  2.39399368e-03+0.00000000e+00j
  4.30905232e-04+0.00000000e+00j  2.13387715e-04+0.00000000e+00j
  8.01094298e-05-8.10593014e-05j  8.01094298e-05+8.10593014e-05j
  2.70609855e-05-4.00793681e-05j  2.70609855e-05+4.00793681e-05j
  2.11777694e-05-6.11980190e-06j  2.11777694e-05+6.11980190e-06j
  1.28768708e-05+0.000000

In [8]:
from koopmanlib.solver_1 import KoopmanDLSolver # resDMD solver using regression
solver = KoopmanDLSolver(dic=basis_function,
                         target_dim=np.shape(data_train)[-1],
                         reg=0.1)

solver.build(data_train=data_train,
             data_valid=data_valid,
             epochs=3000,
             batch_size=5000,
             lr=1e-6,
             log_interval=10,
             lr_decay_factor=.8)

Epoch 1/2
2/2 [==============================] - 31s 5s/step - loss: 0.7167 - val_loss: 0.7186
Epoch 2/2
2/2 [==============================] - 1s 304ms/step - loss: 0.7188 - val_loss: 0.7216
number of the outer loop: 0
Epoch 1/2
2/2 [==============================] - 1s 339ms/step - loss: 0.7237 - val_loss: 0.7235
Epoch 2/2
2/2 [==============================] - 1s 311ms/step - loss: 0.7093 - val_loss: 0.7262
number of the outer loop: 1
Epoch 1/2
2/2 [==============================] - 1s 329ms/step - loss: 0.7089 - val_loss: 0.7196
Epoch 2/2
2/2 [==============================] - 1s 305ms/step - loss: 0.7202 - val_loss: 0.7304
number of the outer loop: 2
Epoch 1/2
2/2 [==============================] - 1s 330ms/step - loss: 0.7282 - val_loss: 0.7243
Epoch 2/2
2/2 [==============================] - 1s 322ms/step - loss: 0.7170 - val_loss: 0.7125
number of the outer loop: 3
Epoch 1/2
2/2 [==============================] - 1s 328ms/step - loss: 0.7130 - val_loss: 0.7284
Epoch 2/2
2/2 [==

In [9]:
evalues = solver.eigenvalues.T
efuns = solver.eigenfunctions(X)
kpm_modes = solver.compute_mode().T
N_dict = np.shape(evalues)[0]

resDMD_DL_outputs1 = {
    'resDMD_DL_outputs':{
    'efuns': efuns,
    'evalues': evalues,
    'kpm_modes': kpm_modes,
    'N_dict':N_dict
    }
}

print(resDMD_DL_outputs1['resDMD_DL_outputs']['evalues'])
print(resDMD_DL_outputs1['resDMD_DL_outputs']['efuns'].shape)

[ 1.01397532e+00+0.00000000e+00j  9.99998631e-01+0.00000000e+00j
  8.42989983e-01+1.54957845e-01j  8.42989983e-01-1.54957845e-01j
  7.72322406e-01+3.74902415e-01j  7.72322406e-01-3.74902415e-01j
  6.53584958e-01-2.95346246e-01j  6.53584958e-01+2.95346246e-01j
  4.47137122e-01+4.97581610e-01j  4.47137122e-01-4.97581610e-01j
  2.69982379e-01-7.70634768e-02j  2.69982379e-01+7.70634768e-02j
  1.76221990e-01+6.78478262e-01j  1.76221990e-01-6.78478262e-01j
  8.16011307e-02+1.79662096e-01j  8.16011307e-02-1.79662096e-01j
  3.20633359e-02+0.00000000e+00j  2.42728950e-02+0.00000000e+00j
  1.15711217e-02+2.20058434e-03j  1.15711217e-02-2.20058434e-03j
  3.81456183e-03+0.00000000e+00j  2.54329556e-03+0.00000000e+00j
  4.95810174e-04+0.00000000e+00j  2.50407718e-04+0.00000000e+00j
  9.11294149e-05+9.07731230e-05j  9.11294149e-05-9.07731230e-05j
  3.16465096e-05-5.30484380e-05j  3.16465096e-05+5.30484380e-05j
  2.21757069e-05+7.28298196e-06j  2.21757069e-05-7.28298196e-06j
  9.57922795e-06+0.000000

In [10]:
from koopmanlib.solver_2 import KoopmanDLSolver # resDMD solver using regression
solver = KoopmanDLSolver(dic=basis_function,
                         target_dim=np.shape(data_train)[-1],
                         reg=0.1)

solver.build(data_train=data_train,
             data_valid=data_valid,
             epochs=3000,
             batch_size=5000,
             lr=1e-6,
             log_interval=10,
             lr_decay_factor=.8)

Epoch 1/2
2/2 [==============================] - 1s 290ms/step - loss: 1.6471 - val_loss: 1.5473
Epoch 2/2
2/2 [==============================] - 0s 118ms/step - loss: 1.6548 - val_loss: 1.5347
number of the outer loop: 0
Epoch 1/2
2/2 [==============================] - 0s 142ms/step - loss: 1.6507 - val_loss: 1.5222
Epoch 2/2
2/2 [==============================] - 0s 111ms/step - loss: 1.6482 - val_loss: 1.5105
number of the outer loop: 1
Epoch 1/2
2/2 [==============================] - 0s 135ms/step - loss: 1.6324 - val_loss: 1.4998
Epoch 2/2
2/2 [==============================] - 0s 113ms/step - loss: 1.6151 - val_loss: 1.4893
number of the outer loop: 2
Epoch 1/2
2/2 [==============================] - 0s 140ms/step - loss: 1.6055 - val_loss: 1.4786
Epoch 2/2
2/2 [==============================] - 0s 114ms/step - loss: 1.5942 - val_loss: 1.4681
number of the outer loop: 3
Epoch 1/2
2/2 [==============================] - 0s 137ms/step - loss: 1.5977 - val_loss: 1.4581
Epoch 2/2
2/2 [

In [11]:
evalues = solver.eigenvalues.T
efuns = solver.eigenfunctions(X)
kpm_modes = solver.compute_mode().T
N_dict = np.shape(evalues)[0]

resDMD_DL_outputs2 = {
    'resDMD_DL_outputs':{
    'efuns': efuns,
    'evalues': evalues,
    'kpm_modes': kpm_modes,
    'N_dict':N_dict
    }
}

print(resDMD_DL_outputs2['resDMD_DL_outputs']['evalues'])
print(resDMD_DL_outputs2['resDMD_DL_outputs']['efuns'].shape)

[ 1.00514891e+00+0.00000000e+00j  9.99998610e-01+0.00000000e+00j
  8.30358669e-01+1.50810604e-01j  8.30358669e-01-1.50810604e-01j
  7.64411440e-01+3.60288553e-01j  7.64411440e-01-3.60288553e-01j
  5.66195314e-01-2.95279153e-01j  5.66195314e-01+2.95279153e-01j
  4.78869818e-01-4.34633036e-01j  4.78869818e-01+4.34633036e-01j
  2.81062956e-01+0.00000000e+00j  1.94899914e-01-1.49575981e-01j
  1.94899914e-01+1.49575981e-01j  1.65279757e-01+6.67085860e-01j
  1.65279757e-01-6.67085860e-01j  6.49127984e-02+0.00000000e+00j
  1.78075812e-02+0.00000000e+00j  9.87099837e-03+0.00000000e+00j
  2.03847251e-03+0.00000000e+00j  9.74842717e-04-2.52849321e-03j
  9.74842717e-04+2.52849321e-03j  9.64204603e-04+0.00000000e+00j
  6.75543322e-04-1.35091377e-03j  6.75543322e-04+1.35091377e-03j
  4.60487609e-04+0.00000000e+00j  9.96353146e-05-1.72743878e-04j
  9.96353146e-05+1.72743878e-04j  3.66420930e-05+0.00000000e+00j
  1.77899629e-05-1.78110239e-05j  1.77899629e-05+1.78110239e-05j
  1.43575462e-05-2.333099

In [12]:
from koopmanlib.solver_3 import KoopmanDLSolver # resDMD solver using regression
solver = KoopmanDLSolver(dic=basis_function,
                         target_dim=np.shape(data_train)[-1],
                         reg=0.1)

solver.build(data_train=data_train,
             data_valid=data_valid,
             epochs=3000,
             batch_size=5000,
             lr=1e-6,
             log_interval=10,
             lr_decay_factor=.8)

Epoch 1/2
2/2 [==============================] - 1s 263ms/step - loss: 1.0739e-08 - val_loss: 1.4245e-08
Epoch 2/2
2/2 [==============================] - 0s 105ms/step - loss: 1.0637e-08 - val_loss: 1.4249e-08
number of the outer loop: 0
Epoch 1/2
2/2 [==============================] - 0s 122ms/step - loss: 1.0936e-08 - val_loss: 1.4184e-08
Epoch 2/2
2/2 [==============================] - 0s 110ms/step - loss: 1.0475e-08 - val_loss: 1.4150e-08
number of the outer loop: 1
Epoch 1/2
2/2 [==============================] - 0s 138ms/step - loss: 1.0370e-08 - val_loss: 1.4154e-08
Epoch 2/2
2/2 [==============================] - 0s 99ms/step - loss: 1.0527e-08 - val_loss: 1.4127e-08
number of the outer loop: 2
Epoch 1/2
2/2 [==============================] - 0s 126ms/step - loss: 1.0519e-08 - val_loss: 1.4126e-08
Epoch 2/2
2/2 [==============================] - 0s 105ms/step - loss: 1.1063e-08 - val_loss: 1.4120e-08
number of the outer loop: 3
Epoch 1/2
2/2 [==============================] - 

In [13]:
evalues = solver.eigenvalues.T
efuns = solver.eigenfunctions(X)
kpm_modes = solver.compute_mode().T
N_dict = np.shape(evalues)[0]

resDMD_DL_outputs3 = {
    'resDMD_DL_outputs':{
    'efuns': efuns,
    'evalues': evalues,
    'kpm_modes': kpm_modes,
    'N_dict':N_dict
    }
}

print(resDMD_DL_outputs3['resDMD_DL_outputs']['evalues'])
print(resDMD_DL_outputs3['resDMD_DL_outputs']['efuns'].shape)

[ 1.00485966e+00+0.00000000e+00j  9.99998700e-01+0.00000000e+00j
  8.30099472e-01+1.50895410e-01j  8.30099472e-01-1.50895410e-01j
  7.62488040e-01+3.59370183e-01j  7.62488040e-01-3.59370183e-01j
  5.59582052e-01+3.01184755e-01j  5.59582052e-01-3.01184755e-01j
  4.77928729e-01+4.27689974e-01j  4.77928729e-01-4.27689974e-01j
  2.82710413e-01+0.00000000e+00j  2.36135956e-01-1.19178752e-01j
  2.36135956e-01+1.19178752e-01j  1.64337845e-01+6.65664828e-01j
  1.64337845e-01-6.65664828e-01j  4.70547965e-02+0.00000000e+00j
  1.73829892e-02+1.05880300e-03j  1.73829892e-02-1.05880300e-03j
  3.64056996e-03-8.35743157e-04j  3.64056996e-03+8.35743157e-04j
  2.90456446e-03+0.00000000e+00j  1.67404226e-03+0.00000000e+00j
  4.78338817e-04-2.33692317e-03j  4.78338817e-04+2.33692317e-03j
  1.49507148e-04+1.14825454e-04j  1.49507148e-04-1.14825454e-04j
  8.71444620e-05+1.79100024e-04j  8.71444620e-05-1.79100024e-04j
  5.09744812e-05+3.12457465e-05j  5.09744812e-05-3.12457465e-05j
  2.44728174e-05+0.000000

In [14]:
from koopmanlib.solver_4 import KoopmanDLSolver # resDMD solver using regression
solver = KoopmanDLSolver(dic=basis_function,
                         target_dim=np.shape(data_train)[-1],
                         reg=0.1)

solver.build(data_train=data_train,
             data_valid=data_valid,
             epochs=3000,
             batch_size=5000,
             lr=1e-6,
             log_interval=10,
             lr_decay_factor=.8)

Epoch 1/2
2/2 [==============================] - 1s 273ms/step - loss: 1.8668 - val_loss: 3.0491
Epoch 2/2
2/2 [==============================] - 0s 98ms/step - loss: 3.0122 - val_loss: 3.9746
number of the outer loop: 0
Epoch 1/2
2/2 [==============================] - 0s 126ms/step - loss: 1.0737 - val_loss: 3.3017
Epoch 2/2
2/2 [==============================] - 0s 101ms/step - loss: 1.0267 - val_loss: 4.6900
number of the outer loop: 1
Epoch 1/2
2/2 [==============================] - 0s 123ms/step - loss: 3.9712 - val_loss: 4.0934
Epoch 2/2
2/2 [==============================] - 0s 104ms/step - loss: 0.4589 - val_loss: 3.8150
number of the outer loop: 2
Epoch 1/2
2/2 [==============================] - 0s 124ms/step - loss: 0.8802 - val_loss: 0.0314
Epoch 2/2
2/2 [==============================] - 0s 100ms/step - loss: 3.1992 - val_loss: 2.6929
number of the outer loop: 3
Epoch 1/2
2/2 [==============================] - 0s 124ms/step - loss: 4.0840 - val_loss: 4.0631
Epoch 2/2
2/2 [=

In [15]:
evalues = solver.eigenvalues.T
efuns = solver.eigenfunctions(X)
kpm_modes = solver.compute_mode().T
N_dict = np.shape(evalues)[0]

resDMD_DL_outputs4 = {
    'resDMD_DL_outputs':{
    'efuns': efuns,
    'evalues': evalues,
    'kpm_modes': kpm_modes,
    'N_dict':N_dict
    }
}

print(resDMD_DL_outputs4['resDMD_DL_outputs']['evalues'])
print(resDMD_DL_outputs4['resDMD_DL_outputs']['efuns'].shape)

[ 1.00481658e+00+0.00000000e+00j  9.99998695e-01+0.00000000e+00j
  8.29996935e-01+1.50764154e-01j  8.29996935e-01-1.50764154e-01j
  7.62732251e-01+3.59913284e-01j  7.62732251e-01-3.59913284e-01j
  5.60926353e-01+2.98031320e-01j  5.60926353e-01-2.98031320e-01j
  4.77927901e-01+4.30339894e-01j  4.77927901e-01-4.30339894e-01j
  2.68438397e-01+0.00000000e+00j  2.37488598e-01+1.11034081e-01j
  2.37488598e-01-1.11034081e-01j  1.64276109e-01+6.65967764e-01j
  1.64276109e-01-6.65967764e-01j  5.71582976e-02+0.00000000e+00j
  1.57244860e-02-2.97981562e-03j  1.57244860e-02+2.97981562e-03j
  5.41398937e-03+0.00000000e+00j  3.59133000e-03+0.00000000e+00j
  2.88530723e-03+0.00000000e+00j  1.39753655e-03+0.00000000e+00j
  1.93215050e-04+0.00000000e+00j  1.18552858e-04+1.61505585e-04j
  1.18552858e-04-1.61505585e-04j  6.17574549e-05+1.01405207e-04j
  6.17574549e-05-1.01405207e-04j  2.97828103e-05+3.62148112e-06j
  2.97828103e-05-3.62148112e-06j  1.13824055e-05+0.00000000e+00j
  8.16583611e-06+0.000000